# Using Nijta API for Voice Anonymization

In this notebook, we demonstrate how to use the API for speech anonymization. We provide a step-by-step guide on how to send a request to the API, process the results, and save the anonymized audio files.

## Prerequisites

Before you begin, make sure you have the following:

- API Token: Obtain your API token by contacting us contact@nijta.com
- Our utility `nijtaio` python library that you can install using the following command: `pip install nijtaio`

In [1]:
import json
import time
from IPython import display

import nijtaio

In [2]:
API_URL = 'https://api.nijta.com/' 
TOKEN = '<your-token>'

## Step 1: Start a session

Before making requests to the API, start a session and obtain a session ID using your token. 
This session ID will be used for subsequent requests.

In [3]:
session_id = nijtaio.session(TOKEN, api_url=API_URL)

## Step 2: Define the Parameters
In this step, we set up the parameters that will be sent along with the request to choose how the voice anonymization will be performed.

The parameters are defined in a dictionary, which is then converted to a JSON string:

- language: in this version, only `french_8` (French/8KHz) and `english_16` (English/16KHz) are available
- gender: the gender you want the result to sound like. 'f' for 'female' or 'm' for 'male'
- robotic (optional): by default, the original variations of the pitch are preserved. With this option turned on, they are removed and the results sounds "robotic"
- content (optional) and mask (optional): if you want to remove sensitive content (see dedicated section below)

In [4]:
params = {
    'language': 'english_16',
    'gender': 'f',
    'robotic': 'false',
    'mask': 'silence',
    'voice': True,
    'content': True
}

## Step 3: Send the Request to the API

We use the `nijtaio.send_request` function to send our audio files for anonymization. 
This function takes as input a list of files, or a folder, or an archive.
The API will process the request and sends back some information about the task:
- the status of the task submission among: 
    - `success` if the batch have been successfully submitted, 
    - `partly success` if some files have been rejected
    - `failed` if the batch could not be submitted
- the name of the files that are not valid and have not been submitted, if any
- the submission time
- the id of the task for monitoring the progress and retrieving the result

In [5]:
# Send request to the API
response = nijtaio.send_request("../samples", params, session_id, 
                                headers={"Content-Type": "application/json; charset=utf-8", "TOKEN":TOKEN},
                                api_url=API_URL)
json.loads(response.content)


{'data': {'task_id': 'e9d8c38b-f218-4508-a927-2d8e9b96cabd'},
 'failed_files': [],
 'submission status': 'success',
 'submission_time': '1691961903.4721053'}

In [6]:
task_id = json.loads(response.content)['data']['task_id']

## Step 3: Monitor Task Status
Check the status of your task using this task ID. Once the task is marked as 'finished,' you can proceed to retrieve and process the results.

In [7]:
# Wait for the batch to be processed
while True:
    time.sleep(1)
    status, anonymized_batch = nijtaio.read_response(task_id, api_url=API_URL)
    if status == 'finished':
        break

## Step 4: Get the Results
`anonymized_batch` is a dictionary with original file paths as keys and anonymized content as values.
If the 'voice' parameter is set to True, the anonymized audio can be retreive with the key 'audio'.
If the 'content' parameter is set to True, the anonymized transcription can be retreive with the key 'transcription'.

In [8]:
for filename in anonymized_batch:
    print("Original")
    display.display(display.Audio(filename))
    print("Anonymized")
    display.display(display.Audio(anonymized_batch[filename]['audio']))
    print(anonymized_batch[filename]['transcription'])

Original


Anonymized


Hey my name is <PER> I am from <LOC> I was born on <DIGIT> March <DIGIT> My credit card number is <DIGIT>
